In [282]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import folium
from sklearn.cluster import DBSCAN
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [283]:
df = pd.read_csv('AB_US_2020.csv')
df

/var/folders/_k/w9l87gnd6j97p2gthl_578lc0000gn/T/ipykernel_9221/852503082.py:1: DtypeWarning:

Columns (4) have mixed types. Specify dtype option on import or set low_memory=False.



id                                               name  \
0          38585    Charming Victorian home - twin beds + breakfast   
1          80905                                   French Chic Loft   
2         108061  Walk to stores/parks/downtown. Fenced yard/Pet...   
3         155305                 Cottage! BonPaul + Sharky's Hostel   
4         160594                                Historic Grove Park   
...          ...                                                ...   
226025  45506143                          DC Hidden In Plain "Site"   
226026  45511428  DC 3 BR w/ screen porch 3 blck to metro w/ par...   
226027  45514685  Charming Penthouse Apt w/ Rooftop Terrace in L...   
226028  45516412                Adams Morgan/Nat'l Zoo 1 BR Apt #32   
226029  45517735    Beautiful large one-bedroom w/ washer and dryer   

          host_id  host_name neighbourhood_group  \
0          165529    Evelyne                 NaN   
1          427027    Celeste                 NaN   
2          320564       Lisa                 NaN   
3          746673    BonPaul                 NaN   
4          769252  Elizabeth                 NaN   
...           ...        ...                 ...   
226025   25973146      Marci                 NaN   
226026  231133074     Thomas                 NaN   
226027   33758935     Bassem                 NaN   
226028   23193071    Michael                 NaN   
226029   17789858       Adam                 NaN   

                                            neighbourhood   latitude  \
0                                                   28804  35.651460   
1                                                   28801  35.597790   
2                                                   28801  35.606700   
3                                                   28806  35.578640   
4                                                   28801  35.614420   
...                                                   ...        ...   
226025  Downtown, Chinatown, Penn Quarters, Mount Vern...  38.903880   
226026                      Brookland, Brentwood, Langdon  38.920820   
226027                                 Shaw, Logan Circle  38.911170   
226028     Kalorama Heights, Adams Morgan, Lanier Heights  38.926630   
226029  Edgewood, Bloomingdale, Truxton Circle, Eckington  38.911569   

        longitude        room_type  price  minimum_nights  number_of_reviews  \
0      -82.627920     Private room     60               1                138   
1      -82.555400  Entire home/apt    470               1                114   
2      -82.555630  Entire home/apt     75              30                 89   
3      -82.595780  Entire home/apt     90               1                267   
4      -82.541270     Private room    125              30                 58   
...           ...              ...    ...             ...                ...   
226025 -77.029730  Entire home/apt    104               1                  0   
226026 -76.990980  Entire home/apt    151               2                  0   
226027 -77.033540  Entire home/apt    240               2                  0   
226028 -77.044360  Entire home/apt     60              21                  0   
226029 -77.009431  Entire home/apt     79               7                  0   

       last_review  reviews_per_month  calculated_host_listings_count  \
0         16/02/20               1.14                               1   
1         07/09/20               1.03                              11   
2         30/11/19               0.81                               2   
3         22/09/20               2.39                               5   
4         19/10/15               0.52                               1   
...            ...                ...                             ...   
226025         NaN                NaN                               2   
226026         NaN                NaN                               1   
226027         NaN                NaN                

In [284]:
df = df[['latitude', 'longitude', 'city']]
df

latitude  longitude             city
0       35.651460 -82.627920        Asheville
1       35.597790 -82.555400        Asheville
2       35.606700 -82.555630        Asheville
3       35.578640 -82.595780        Asheville
4       35.614420 -82.541270        Asheville
...           ...        ...              ...
226025  38.903880 -77.029730  Washington D.C.
226026  38.920820 -76.990980  Washington D.C.
226027  38.911170 -77.033540  Washington D.C.
226028  38.926630 -77.044360  Washington D.C.
226029  38.911569 -77.009431  Washington D.C.

[226030 rows x 3 columns]

In [285]:
df['city'].unique()

array(['Asheville', 'Austin', 'Boston', 'Broward County', 'Cambridge',
       'Chicago', 'Clark County', 'Columbus', 'Denver', 'Hawaii',
       'Jersey City', 'Los Angeles', 'Nashville', 'New Orleans',
       'New York City', 'Oakland', 'Pacific Grove', 'Portland',
       'Rhode Island', 'Salem', 'San Clara Country', 'San Diego',
       'San Francisco', 'San Mateo County', 'Santa Cruz County',
       'Seattle', 'Twin Cities MSA', 'Washington D.C.'], dtype=object)

In [286]:
locations = ['New York City', 'Chicago', 'Seattle', 'San Francisco', 'Clark County', 'San Mateo County', 'Santa Cruz County', 'Asheville', 'Pacific Grove']

df = df[df['city'].isin(locations)]

In [287]:
df['city'].value_counts()

city
New York City        45756
Clark County          8408
San Francisco         7053
Seattle               6575
Chicago               6397
San Mateo County      2855
Asheville             2074
Santa Cruz County     1571
Pacific Grove          179
Name: count, dtype: int64

In [288]:
df

latitude   longitude       city
0       35.651460  -82.627920  Asheville
1       35.597790  -82.555400  Asheville
2       35.606700  -82.555630  Asheville
3       35.578640  -82.595780  Asheville
4       35.614420  -82.541270  Asheville
...           ...         ...        ...
212205  47.624490 -122.335400    Seattle
212206  47.615020 -122.342490    Seattle
212207  47.639570 -122.360840    Seattle
212208  47.615070 -122.340490    Seattle
212209  47.660222 -122.316817    Seattle

[80868 rows x 3 columns]

In [34]:
lat, long = df.latitude, df.longitude

fig = px.scatter(x=long, y=lat, color=df['city'])
fig.show()

In [35]:
# eps_km = 0.5/6371
# min_samples = 10


# cities = df['city'].unique()
# results = []

# for city in  cities:
#     subset = df[df['city'] == city]
#     radians = np.radians(subset[['latitude', 'longitude']])
    
#     db = DBSCAN(eps=eps_km, min_samples=min_samples, metric='harvesine', algorithm='ball_tree')
#     subset['cluster'] = db.fit_predict(radians)

#     clustered = subset[subset]


In [36]:
eps_km = 0.29/6371
min_samples = 14

df_ny = df[df['city'] == 'New York City']
coords = df_ny[['latitude', 'longitude']].values

db = DBSCAN(eps=eps_km, min_samples=min_samples, algorithm='auto', metric='haversine').fit(np.radians(coords))
cluster_labels = db.labels_

n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0) 


In [37]:
n_clusters

50

In [38]:
lon, lat = df_ny.longitude, df_ny.latitude
fig = px.scatter(x=lon, y=lat, color=cluster_labels)


fig.show()

In [39]:
df_ny['latitude'].dtype

dtype('float64')

In [40]:
df_ny['cluster'] = cluster_labels
df_ny['cluster'].value_counts() 

/var/folders/_k/w9l87gnd6j97p2gthl_578lc0000gn/T/ipykernel_9221/2678974179.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



cluster
 0     20200
 1     17043
-1      3579
 2      2907
 7       134
 12      123
 21      112
 10      109
 11      103
 8       101
 15       93
 5        88
 13       79
 9        73
 6        58
 27       57
 17       54
 19       53
 4        47
 35       37
 42       37
 36       34
 34       34
 30       32
 41       32
 25       31
 18       29
 23       28
 33       28
 48       28
 31       28
 14       24
 22       24
 24       24
 46       24
 39       22
 20       21
 16       21
 32       20
 3        19
 44       19
 47       18
 28       18
 40       16
 45       16
 37       15
 29       15
 43       14
 26       14
 38       12
 49        9
Name: count, dtype: int64

In [41]:
df_ny.loc[:, 'cluster'] = cluster_labels

# Generate representative points for each cluster (e.g., centroids)
# This is a simple way to get a central point - mean latitude and longitude of the cluster
centroids = df_ny.groupby('cluster')[['latitude', 'longitude']].mean()

print(f"Number of clusters: {n_clusters}")
print(centroids)

Number of clusters: 50
          latitude  longitude
cluster                      
-1       40.717426 -73.879828
 0       40.765209 -73.974661
 1       40.689437 -73.950625
 2       40.754296 -73.912692
 3       40.672012 -73.765388
 4       40.644546 -74.082259
 5       40.763376 -73.948573
 6       40.586819 -73.814655
 7       40.673955 -73.890158
 8       40.633187 -74.026378
 9       40.578359 -73.960621
 10      40.728501 -73.856103
 11      40.757163 -73.818830
 12      40.750787 -73.830514
 13      40.622061 -74.028232
 14      40.821328 -73.927798
 15      40.688088 -73.871806
 16      40.855223 -73.865556
 17      40.830631 -73.920381
 18      40.764388 -73.829243
 19      40.590118 -73.794190
 20      40.624491 -73.961736
 21      40.766492 -73.872617
 22      40.849757 -73.903007
 23      40.599194 -73.958164
 24      40.707910 -73.830750
 25      40.884393 -73.905381
 26      40.689474 -73.853549
 27      40.673256 -73.877865
 28      40.813478 -73.888335
 29      40.66167

In [42]:
centroids

latitude  longitude
cluster                      
-1       40.717426 -73.879828
 0       40.765209 -73.974661
 1       40.689437 -73.950625
 2       40.754296 -73.912692
 3       40.672012 -73.765388
 4       40.644546 -74.082259
 5       40.763376 -73.948573
 6       40.586819 -73.814655
 7       40.673955 -73.890158
 8       40.633187 -74.026378
 9       40.578359 -73.960621
 10      40.728501 -73.856103
 11      40.757163 -73.818830
 12      40.750787 -73.830514
 13      40.622061 -74.028232
 14      40.821328 -73.927798
 15      40.688088 -73.871806
 16      40.855223 -73.865556
 17      40.830631 -73.920381
 18      40.764388 -73.829243
 19      40.590118 -73.794190
 20      40.624491 -73.961736
 21      40.766492 -73.872617
 22      40.849757 -73.903007
 23      40.599194 -73.958164
 24      40.707910 -73.830750
 25      40.884393 -73.905381
 26      40.689474 -73.853549
 27      40.673256 -73.877865
 28      40.813478 -73.888335
 29      40.661677 -73.770073
 30      40.696088 -73.849727
 31      40.635089 -74.080878
 32      40.608486 -73.974545
 33      40.607641 -73.954274
 34      40.637707 -73.911771
 35      40.654372 -73.731431
 36      40.671405 -73.778927
 37      40.610454 -73.960015
 38      40.831656 -73.928800
 39      40.645820 -73.902939
 40      40.686503 -73.789391
 41      40.760946 -73.766647
 42      40.655908 -73.918017
 43      40.694350 -73.827547
 44      40.837119 -73.858727
 45      40.634849 -74.005778
 46      40.661090 -73.891143
 47      40.843607 -73.907546
 48      40.750670 -73.866705
 49      40.655401 -73.927803

In [49]:
centroids['cluster'] = centroids.index

In [52]:
centroids.drop(-1, axis=0, inplace=True)

In [324]:
latt, longg = centroids.latitude, centroids.longitude

fig = px.scatter(x=longg, y=latt, color=centroids['cluster'])

fig.update_layout(
    title='New York Route Centroids',
    title_x=0.5,  # Center the title
    xaxis_title='Longitude',
    yaxis_title='Latitude',
    legend_title='Routes')
fig.show()

In [54]:
centroids['city'] = 'New York City'

In [57]:
final_df = centroids.copy() 

#### This function takes our dataframe and returns a dataframe of centroids for the selected city

In [80]:
def cluster_and_extract_centroids(df, city_name, eps, min_samples):
    # Filter the dataset for the city
    city_data = df[df['city'] == city_name]
    coords = city_data[['latitude', 'longitude']].values

    # Perform DBSCAN clustering
    dbscan = DBSCAN(eps=eps, min_samples=min_samples, algorithm='auto', metric='haversine').fit(np.radians(coords))
    cluster_labels = dbscan.labels_
    
    # Filter out outliers
    city_data_filtered = city_data[cluster_labels != -1]
    cluster_labels_filtered = cluster_labels[cluster_labels != -1]
    
    # Extract centroids
    centroids_df = city_data_filtered.groupby(cluster_labels_filtered)[['latitude', 'longitude']].mean()
    centroids_df['cluster'] = centroids_df.index
    centroids_df['city'] = city_name
    
    return centroids_df.reset_index(drop=True)

In [ ]:
#{state} : [{eps}, {min samples}]
required_hyperparams = {
    'San Francisco': [0.29/6371, 14],
    'Clark County': [0.35/6371, 10],
    'Chicago': [0.28/6371, 7],
    'Seattle': [0.269/6371, 7],
    'Asheville': [0.3/6371, 6],
    'San Mateo County': [0.3/6371, 10],
    'Santa Cruz County': [0.19/6371, 5],
    'Pacific Grove': [0.072/6371, 2]
}

In [81]:
sf_centroids = cluster_and_extract_centroids(df, 'San Francisco', 0.12/6371, 9)
cc_centroids = cluster_and_extract_centroids(df, 'Clark County', 0.35/6371, 10)
chicago_centroids = cluster_and_extract_centroids(df, 'Chicago', 0.28/6371, 7)

sf_centroids

latitude   longitude  cluster           city
0   37.771909 -122.433082        0  San Francisco
1   37.765428 -122.451562        1  San Francisco
2   37.758355 -122.414749        2  San Francisco
3   37.775061 -122.423693        3  San Francisco
4   37.788096 -122.410278        4  San Francisco
..        ...         ...      ...            ...
78  37.717350 -122.456238       78  San Francisco
79  37.775583 -122.456469       79  San Francisco
80  37.712031 -122.442718       80  San Francisco
81  37.736368 -122.397710       81  San Francisco
82  37.747599 -122.431518       82  San Francisco

[83 rows x 4 columns]

In [292]:
cc_centroids = cluster_and_extract_centroids(df, 'Clark County', 0.35/6371, 10)
cc_centroids

latitude   longitude  cluster          city
0   36.110878 -115.177148        0  Clark County
1   36.098710 -115.214272        1  Clark County
2   36.059319 -115.170355        2  Clark County
3   36.110856 -115.280891        3  Clark County
4   36.126482 -115.147322        4  Clark County
..        ...         ...      ...           ...
68  36.055572 -115.082038       68  Clark County
69  36.155571 -115.187634       69  Clark County
70  36.040224 -115.112477       70  Clark County
71  36.090997 -115.249406       71  Clark County
72  35.958875 -115.183968       72  Clark County

[73 rows x 4 columns]

In [294]:
chicago_centroids = cluster_and_extract_centroids(df, 'Chicago',0.28/6371, 7)
chicago_centroids

latitude  longitude  cluster     city
0   41.855177 -87.695751        0  Chicago
1   41.912237 -87.688987        1  Chicago
2   41.909275 -87.641283        2  Chicago
3   41.800368 -87.598900        3  Chicago
4   41.974606 -87.666038        4  Chicago
..        ...        ...      ...      ...
58  41.795204 -87.661207       58  Chicago
59  42.015561 -87.681928       59  Chicago
60  41.996542 -87.701556       60  Chicago
61  41.743929 -87.545814       61  Chicago
62  41.760269 -87.564203       62  Chicago

[63 rows x 4 columns]

In [295]:
seattle_centroids = cluster_and_extract_centroids(df, 'Seattle', 0.269/6371, 7)
seattle_centroids

latitude   longitude  cluster     city
0   47.615826 -122.329184        0  Seattle
1   47.550286 -122.318361        1  Seattle
2   47.550513 -122.380957        2  Seattle
3   47.670703 -122.346114        3  Seattle
4   47.566375 -122.366648        4  Seattle
..        ...         ...      ...      ...
58  47.712156 -122.283219       58  Seattle
59  47.661656 -122.268815       59  Seattle
60  47.532358 -122.290625       60  Seattle
61  47.573744 -122.387400       61  Seattle
62  47.724546 -122.334611       62  Seattle

[63 rows x 4 columns]

In [296]:
asheville_centroids = cluster_and_extract_centroids(df, 'Asheville', 0.3/6371, 6)
asheville_centroids

latitude  longitude  cluster       city
0   35.600075 -82.555108        0  Asheville
1   35.578474 -82.584272        1  Asheville
2   35.613289 -82.541999        2  Asheville
3   35.597944 -82.505356        3  Asheville
4   35.574808 -82.557792        4  Asheville
5   35.582362 -82.560194        5  Asheville
6   35.627163 -82.581225        6  Asheville
7   35.575068 -82.536601        7  Asheville
8   35.586560 -82.503084        8  Asheville
9   35.625961 -82.529635        9  Asheville
10  35.582836 -82.607824       10  Asheville
11  35.630490 -82.576498       11  Asheville
12  35.612156 -82.525259       12  Asheville
13  35.596360 -82.593413       13  Asheville
14  35.589723 -82.620225       14  Asheville
15  35.548693 -82.480372       15  Asheville
16  35.603292 -82.469791       16  Asheville
17  35.607833 -82.487436       17  Asheville
18  35.568926 -82.614914       18  Asheville
19  35.566834 -82.525001       19  Asheville
20  35.554543 -82.476553       20  Asheville
21  35.475039 -82.503767       21  Asheville
22  35.490725 -82.512048       22  Asheville
23  35.551511 -82.508770       23  Asheville
24  35.522457 -82.613499       24  Asheville
25  35.565250 -82.540456       25  Asheville
26  35.557488 -82.492414       26  Asheville
27  35.553472 -82.623267       27  Asheville
28  35.509382 -82.611961       28  Asheville
29  35.626039 -82.521227       29  Asheville
30  35.618656 -82.580626       30  Asheville
31  35.638001 -82.595005       31  Asheville
32  35.555943 -82.502647       32  Asheville
33  35.560399 -82.506429       33  Asheville
34  35.470570 -82.500083       34  Asheville
35  35.639415 -82.519187       35  Asheville
36  35.508864 -82.661161       36  Asheville
37  35.588604 -82.507984       37  Asheville
38  35.469415 -82.575010       38  Asheville
39  35.638118 -82.575582       39  Asheville
40  35.612603 -82.603947       40  Asheville
41  35.591611 -82.470138       41  Asheville
42  35.623638 -82.482483       42  Asheville
43  35.651655 -82.528330       43  Asheville
44  35.627810 -82.598184       44  Asheville
45  35.490933 -82.572926       45  Asheville
46  35.632015 -82.629326       46  Asheville
47  35.622060 -82.476537       47  Asheville
48  35.590084 -82.496262       48  Asheville
49  35.430970 -82.525032       49  Asheville
50  35.575709 -82.639643       50  Asheville
51  35.579438 -82.540605       51  Asheville
52  35.569492 -82.632328       52  Asheville

In [303]:
asheville_centroids = asheville_centroids.drop(asheville_centroids.index[-1])
asheville_centroids

latitude  longitude  cluster       city
0   35.600075 -82.555108        0  Asheville
1   35.578474 -82.584272        1  Asheville
2   35.613289 -82.541999        2  Asheville
3   35.597944 -82.505356        3  Asheville
4   35.574808 -82.557792        4  Asheville
5   35.582362 -82.560194        5  Asheville
6   35.627163 -82.581225        6  Asheville
7   35.575068 -82.536601        7  Asheville
8   35.586560 -82.503084        8  Asheville
9   35.625961 -82.529635        9  Asheville
10  35.582836 -82.607824       10  Asheville
11  35.630490 -82.576498       11  Asheville
12  35.612156 -82.525259       12  Asheville
13  35.596360 -82.593413       13  Asheville
14  35.589723 -82.620225       14  Asheville
15  35.548693 -82.480372       15  Asheville
16  35.603292 -82.469791       16  Asheville
17  35.607833 -82.487436       17  Asheville
18  35.568926 -82.614914       18  Asheville
19  35.566834 -82.525001       19  Asheville
20  35.554543 -82.476553       20  Asheville
21  35.475039 -82.503767       21  Asheville
22  35.490725 -82.512048       22  Asheville
23  35.551511 -82.508770       23  Asheville
24  35.522457 -82.613499       24  Asheville
25  35.565250 -82.540456       25  Asheville
26  35.557488 -82.492414       26  Asheville
27  35.553472 -82.623267       27  Asheville
28  35.509382 -82.611961       28  Asheville
29  35.626039 -82.521227       29  Asheville
30  35.618656 -82.580626       30  Asheville
31  35.638001 -82.595005       31  Asheville
32  35.555943 -82.502647       32  Asheville
33  35.560399 -82.506429       33  Asheville
34  35.470570 -82.500083       34  Asheville
35  35.639415 -82.519187       35  Asheville
36  35.508864 -82.661161       36  Asheville
37  35.588604 -82.507984       37  Asheville
38  35.469415 -82.575010       38  Asheville
39  35.638118 -82.575582       39  Asheville
40  35.612603 -82.603947       40  Asheville
41  35.591611 -82.470138       41  Asheville
42  35.623638 -82.482483       42  Asheville
43  35.651655 -82.528330       43  Asheville
44  35.627810 -82.598184       44  Asheville
45  35.490933 -82.572926       45  Asheville
46  35.632015 -82.629326       46  Asheville
47  35.622060 -82.476537       47  Asheville
48  35.590084 -82.496262       48  Asheville
49  35.430970 -82.525032       49  Asheville
50  35.575709 -82.639643       50  Asheville
51  35.579438 -82.540605       51  Asheville

In [297]:
smc_centroids = cluster_and_extract_centroids(df, 'San Mateo County', 0.3/6371, 10)
smc_centroids

latitude   longitude  cluster              city
0   37.466300 -122.141807        0  San Mateo County
1   37.449402 -122.181969        1  San Mateo County
2   37.509771 -122.264788        2  San Mateo County
3   37.704949 -122.478444        3  San Mateo County
4   37.543973 -122.282431        4  San Mateo County
5   37.704031 -122.461512        5  San Mateo County
6   37.581396 -122.350082        6  San Mateo County
7   37.459374 -122.130980        7  San Mateo County
8   37.477137 -122.157872        8  San Mateo County
9   37.599931 -122.391915        9  San Mateo County
10  37.689313 -122.463218       10  San Mateo County
11  37.701532 -122.491966       11  San Mateo County
12  37.633770 -122.492566       12  San Mateo County
13  37.706222 -122.417304       13  San Mateo County
14  37.682082 -122.479099       14  San Mateo County
15  37.469475 -122.163303       15  San Mateo County
16  37.585058 -122.361520       16  San Mateo County
17  37.481563 -122.227834       17  San Mateo County
18  37.509329 -122.475098       18  San Mateo County
19  37.468364 -122.207011       19  San Mateo County
20  37.705953 -122.432017       20  San Mateo County
21  37.459789 -122.162461       21  San Mateo County
22  37.690163 -122.493245       22  San Mateo County
23  37.474312 -122.231415       23  San Mateo County
24  37.548864 -122.311898       24  San Mateo County
25  37.662395 -122.409812       25  San Mateo County
26  37.570764 -122.321037       26  San Mateo County
27  37.593943 -122.509923       27  San Mateo County
28  37.620794 -122.408917       28  San Mateo County
29  37.485961 -122.183446       29  San Mateo County
30  37.428681 -122.195668       30  San Mateo County
31  37.453091 -122.168975       31  San Mateo County
32  37.647136 -122.456158       32  San Mateo County
33  37.495897 -122.460707       33  San Mateo County
34  37.483644 -122.220465       34  San Mateo County
35  37.474211 -122.222954       35  San Mateo County
36  37.663727 -122.401789       36  San Mateo County
37  37.569061 -122.307056       37  San Mateo County
38  37.625485 -122.446935       38  San Mateo County
39  37.593726 -122.400659       39  San Mateo County
40  37.463801 -122.177717       40  San Mateo County
41  37.669198 -122.436245       41  San Mateo County
42  37.554731 -122.307767       42  San Mateo County
43  37.566297 -122.299581       43  San Mateo County
44  37.611284 -122.401843       44  San Mateo County
45  37.654632 -122.411268       45  San Mateo County
46  37.578718 -122.338303       46  San Mateo County

In [298]:
scc_centroids = cluster_and_extract_centroids(df, 'Santa Cruz County', 0.19/6371, 5)
scc_centroids

latitude   longitude  cluster               city
0   36.958210 -121.974800        0  Santa Cruz County
1   36.965261 -122.000474        1  Santa Cruz County
2   36.953807 -122.045226        2  Santa Cruz County
3   36.961822 -122.026730        3  Santa Cruz County
4   36.957397 -122.034673        4  Santa Cruz County
5   36.975984 -122.010864        5  Santa Cruz County
6   36.969782 -121.903348        6  Santa Cruz County
7   36.975562 -121.917697        7  Santa Cruz County
8   36.973600 -121.951726        8  Santa Cruz County
9   36.974896 -122.030822        9  Santa Cruz County
10  37.044740 -122.019963       10  Santa Cruz County
11  36.967903 -121.896262       11  Santa Cruz County
12  36.967928 -122.033098       12  Santa Cruz County
13  36.951004 -121.876084       13  Santa Cruz County
14  36.971259 -122.026486       14  Santa Cruz County
15  36.966891 -122.022059       15  Santa Cruz County
16  37.036508 -122.144638       16  Santa Cruz County
17  36.966618 -121.889334       17  Santa Cruz County
18  36.965030 -121.985321       18  Santa Cruz County
19  36.967660 -121.874938       19  Santa Cruz County
20  37.040881 -122.077112       20  Santa Cruz County
21  36.853936 -121.811331       21  Santa Cruz County
22  36.962124 -121.893838       22  Santa Cruz County
23  36.971334 -122.007374       23  Santa Cruz County
24  36.928566 -121.858040       24  Santa Cruz County
25  36.872352 -121.821632       25  Santa Cruz County
26  36.866988 -121.818340       26  Santa Cruz County
27  36.971966 -121.981466       27  Santa Cruz County
28  36.963147 -122.052857       28  Santa Cruz County
29  36.982621 -122.014234       29  Santa Cruz County
30  36.953096 -121.869976       30  Santa Cruz County
31  37.050423 -122.056276       31  Santa Cruz County
32  36.921242 -121.854000       32  Santa Cruz County
33  36.971402 -121.971772       33  Santa Cruz County
34  37.049793 -122.060895       34  Santa Cruz County

In [304]:
scc_centroids = scc_centroids.drop(scc_centroids.index[-1])
scc_centroids

latitude   longitude  cluster               city
0   36.958210 -121.974800        0  Santa Cruz County
1   36.965261 -122.000474        1  Santa Cruz County
2   36.953807 -122.045226        2  Santa Cruz County
3   36.961822 -122.026730        3  Santa Cruz County
4   36.957397 -122.034673        4  Santa Cruz County
5   36.975984 -122.010864        5  Santa Cruz County
6   36.969782 -121.903348        6  Santa Cruz County
7   36.975562 -121.917697        7  Santa Cruz County
8   36.973600 -121.951726        8  Santa Cruz County
9   36.974896 -122.030822        9  Santa Cruz County
10  37.044740 -122.019963       10  Santa Cruz County
11  36.967903 -121.896262       11  Santa Cruz County
12  36.967928 -122.033098       12  Santa Cruz County
13  36.951004 -121.876084       13  Santa Cruz County
14  36.971259 -122.026486       14  Santa Cruz County
15  36.966891 -122.022059       15  Santa Cruz County
16  37.036508 -122.144638       16  Santa Cruz County
17  36.966618 -121.889334       17  Santa Cruz County
18  36.965030 -121.985321       18  Santa Cruz County
19  36.967660 -121.874938       19  Santa Cruz County
20  37.040881 -122.077112       20  Santa Cruz County
21  36.853936 -121.811331       21  Santa Cruz County
22  36.962124 -121.893838       22  Santa Cruz County
23  36.971334 -122.007374       23  Santa Cruz County
24  36.928566 -121.858040       24  Santa Cruz County
25  36.872352 -121.821632       25  Santa Cruz County
26  36.866988 -121.818340       26  Santa Cruz County
27  36.971966 -121.981466       27  Santa Cruz County
28  36.963147 -122.052857       28  Santa Cruz County
29  36.982621 -122.014234       29  Santa Cruz County
30  36.953096 -121.869976       30  Santa Cruz County
31  37.050423 -122.056276       31  Santa Cruz County
32  36.921242 -121.854000       32  Santa Cruz County
33  36.971402 -121.971772       33  Santa Cruz County

In [299]:
pcg_centroids = cluster_and_extract_centroids(df, 'Pacific Grove', 0.072/6371, 2)
pcg_centroids

latitude   longitude  cluster           city
0   36.623204 -121.915994        0  Pacific Grove
1   36.603535 -121.927165        1  Pacific Grove
2   36.624657 -121.916600        2  Pacific Grove
3   36.621368 -121.920568        3  Pacific Grove
4   36.615190 -121.922905        4  Pacific Grove
5   36.631735 -121.924415        5  Pacific Grove
6   36.618977 -121.914243        6  Pacific Grove
7   36.618243 -121.910920        7  Pacific Grove
8   36.619495 -121.910000        8  Pacific Grove
9   36.625200 -121.926760        9  Pacific Grove
10  36.622077 -121.921637       10  Pacific Grove
11  36.623947 -121.920967       11  Pacific Grove
12  36.621385 -121.915140       12  Pacific Grove
13  36.634105 -121.924620       13  Pacific Grove
14  36.618335 -121.909585       14  Pacific Grove
15  36.619285 -121.920660       15  Pacific Grove
16  36.617482 -121.919984       16  Pacific Grove
17  36.620325 -121.910455       17  Pacific Grove
18  36.617800 -121.912675       18  Pacific Grove
19  36.620587 -121.907973       19  Pacific Grove
20  36.632545 -121.926910       20  Pacific Grove
21  36.617450 -121.909055       21  Pacific Grove
22  36.621494 -121.918948       22  Pacific Grove
23  36.618120 -121.908110       23  Pacific Grove
24  36.626880 -121.920775       24  Pacific Grove
25  36.619200 -121.912490       25  Pacific Grove
26  36.628643 -121.931543       26  Pacific Grove
27  36.620120 -121.918870       27  Pacific Grove
28  36.622905 -121.918980       28  Pacific Grove

#### modify pcg_centroids df because its one less than we need

In [302]:
pcg_centroids.loc[len(pcg_centroids)] = [36.61691, -121.90609, 29, 'Pacific Grove']
pcg_centroids

latitude   longitude  cluster           city
0   36.623204 -121.915994        0  Pacific Grove
1   36.603535 -121.927165        1  Pacific Grove
2   36.624657 -121.916600        2  Pacific Grove
3   36.621368 -121.920568        3  Pacific Grove
4   36.615190 -121.922905        4  Pacific Grove
5   36.631735 -121.924415        5  Pacific Grove
6   36.618977 -121.914243        6  Pacific Grove
7   36.618243 -121.910920        7  Pacific Grove
8   36.619495 -121.910000        8  Pacific Grove
9   36.625200 -121.926760        9  Pacific Grove
10  36.622077 -121.921637       10  Pacific Grove
11  36.623947 -121.920967       11  Pacific Grove
12  36.621385 -121.915140       12  Pacific Grove
13  36.634105 -121.924620       13  Pacific Grove
14  36.618335 -121.909585       14  Pacific Grove
15  36.619285 -121.920660       15  Pacific Grove
16  36.617482 -121.919984       16  Pacific Grove
17  36.620325 -121.910455       17  Pacific Grove
18  36.617800 -121.912675       18  Pacific Grove
19  36.620587 -121.907973       19  Pacific Grove
20  36.632545 -121.926910       20  Pacific Grove
21  36.617450 -121.909055       21  Pacific Grove
22  36.621494 -121.918948       22  Pacific Grove
23  36.618120 -121.908110       23  Pacific Grove
24  36.626880 -121.920775       24  Pacific Grove
25  36.619200 -121.912490       25  Pacific Grove
26  36.628643 -121.931543       26  Pacific Grove
27  36.620120 -121.918870       27  Pacific Grove
28  36.622905 -121.918980       28  Pacific Grove
29  36.616910 -121.906090       29  Pacific Grove

In [291]:
final_df = pd.concat([final_df, sf_centroids], ignore_index=True)
final_df

['sf_centroids', cc_centroids, chicago_centroids, seattle_centroids, asheville_centroids, smc_centroids, scc_centroids,  ]

latitude   longitude  cluster           city
0    40.765209  -73.974661        0  New York City
1    40.689437  -73.950625        1  New York City
2    40.754296  -73.912692        2  New York City
3    40.672012  -73.765388        3  New York City
4    40.644546  -74.082259        4  New York City
..         ...         ...      ...            ...
128  37.717350 -122.456238       78  San Francisco
129  37.775583 -122.456469       79  San Francisco
130  37.712031 -122.442718       80  San Francisco
131  37.736368 -122.397710       81  San Francisco
132  37.747599 -122.431518       82  San Francisco

[133 rows x 4 columns]

#### concatenate all the centroid data frames together. this is our final output dataframe

In [306]:
all_centroids = [cc_centroids, chicago_centroids, seattle_centroids, asheville_centroids, smc_centroids, scc_centroids, pcg_centroids]

for centroid in all_centroids:
    final_df = pd.concat([final_df, centroid], ignore_index=True)

final_df.drop('cluster', axis=1, inplace=True)
final_df

latitude   longitude               city
0    40.765209  -73.974661      New York City
1    40.689437  -73.950625      New York City
2    40.754296  -73.912692      New York City
3    40.672012  -73.765388      New York City
4    40.644546  -74.082259      New York City
..         ...         ...                ...
460  36.982621 -122.014234  Santa Cruz County
461  36.953096 -121.869976  Santa Cruz County
462  37.050423 -122.056276  Santa Cruz County
463  36.921242 -121.854000  Santa Cruz County
464  36.971402 -121.971772  Santa Cruz County

[465 rows x 3 columns]

In [317]:
final_df

latitude   longitude               city
0    40.765209  -73.974661      New York City
1    40.689437  -73.950625      New York City
2    40.754296  -73.912692      New York City
3    40.672012  -73.765388      New York City
4    40.644546  -74.082259      New York City
..         ...         ...                ...
460  36.982621 -122.014234  Santa Cruz County
461  36.953096 -121.869976  Santa Cruz County
462  37.050423 -122.056276  Santa Cruz County
463  36.921242 -121.854000  Santa Cruz County
464  36.971402 -121.971772  Santa Cruz County

[465 rows x 3 columns]

In [318]:
# final_df = pd.concat([final_df, pcg_centroids], ignore_index=True)
# final_df


latitude   longitude           city
0    40.765209  -73.974661  New York City
1    40.689437  -73.950625  New York City
2    40.754296  -73.912692  New York City
3    40.672012  -73.765388  New York City
4    40.644546  -74.082259  New York City
..         ...         ...            ...
490  36.619200 -121.912490  Pacific Grove
491  36.628643 -121.931543  Pacific Grove
492  36.620120 -121.918870  Pacific Grove
493  36.622905 -121.918980  Pacific Grove
494  36.616910 -121.906090  Pacific Grove

[495 rows x 3 columns]

In [323]:
final_df.to_csv('Constructed_Routes.csv', index=False)

In [84]:
latt, longg = sf_centroids.latitude, sf_centroids.longitude

fig = px.scatter(x=longg, y=latt, color=sf_centroids['cluster'])
fig.update_layout(
    title='San Francisco Route Centroids',
    title_x=0.5,  # Center the title
    xaxis_title='Longitude',
    yaxis_title='Latitude',
    legend_title='Routes')
fig.show()

In [322]:
dfs = [centroids, sf_centroids, cc_centroids, chicago_centroids, seattle_centroids, asheville_centroids, smc_centroids, scc_centroids, pcg_centroids]

# Create a 3x3 subplot layout
fig = make_subplots(rows=3, cols=3, subplot_titles=['New York', 'San Francisco', 'Clark County', 
                                                     'Chicago', 'Seattle', 'Asheville', 
                                                     'San Mateo County', 'Santa Cruz County', 'Pacific Grove'])

# Iterate over the DataFrames and add each to the appropriate subplot
for i, df in enumerate(dfs):
    row = i // 3 + 1
    col = i % 3 + 1
    fig.add_trace(go.Scatter(x=df['longitude'], y=df['latitude'], mode='markers'), row=row, col=col)

# Update layout if necessary (e.g., to add a common title)
fig.update_layout(height=900, width=900, title_x=0.5, title_text="City Routes Centroid Plots")

# Show the figure
fig.show()


In [275]:
# eps_km = 0.0721/6371 #inverse
# min_samples = 2 #inverse 

# df_c = df[df['city'] == 'Pacific Grove']
# coords = df_c[['latitude', 'longitude']].values

# db = DBSCAN(eps=eps_km, min_samples=min_samples, algorithm='auto', metric='haversine').fit(np.radians(coords))
# cluster_labels = db.labels_

# n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0) 
# n_clusters

29

In [228]:
# lonnn, lattt = df_c.longitude, df_c.latitude
# fig = px.scatter(x=lonnn, y=lattt, color=cluster_labels)


# fig.show()

#### lets plot our final datafrmae on map

In [331]:
final_df

latitude   longitude           city
0    40.765209  -73.974661  New York City
1    40.689437  -73.950625  New York City
2    40.754296  -73.912692  New York City
3    40.672012  -73.765388  New York City
4    40.644546  -74.082259  New York City
..         ...         ...            ...
490  36.619200 -121.912490  Pacific Grove
491  36.628643 -121.931543  Pacific Grove
492  36.620120 -121.918870  Pacific Grove
493  36.622905 -121.918980  Pacific Grove
494  36.616910 -121.906090  Pacific Grove

[495 rows x 3 columns]

#### plot geographical data on map

In [326]:
lat_mean = final_df['latitude'].mean()
lon_mean = final_df['longitude'].mean()

m = folium.Map(location=[lat_mean, lon_mean], zoom_start=12)

In [327]:
for index, row in final_df.iterrows():
    folium.Marker(
        [row['latitude'], row['longitude']],
        popup=f"<b>{row['city']}</b>",  # Assuming 'Location' is the column with city names
    ).add_to(m)

In [330]:
m

In [332]:
m.save("my_map.html")